In [15]:
import os
import pandas as pd
import requests
import xml.etree.ElementTree as ET
import time

# Load your CSV
df = pd.read_csv("/Users/bhookhabhaloo/Downloads/CF-FR-equities-01-01-2005-to-22-08-2025.csv")

# Change to your actual XBRL link column name
xbrl_col = "** XBRL"

# Base output directory
os.makedirs("xbrl_csvs", exist_ok=True)

def fetch_with_retry(url, retries=3, timeout=120):
    """Download with retries + timeout"""
    for attempt in range(retries):
        try:
            r = requests.get(url, timeout=timeout)
            r.raise_for_status()
            return r.content
        except Exception as e:
            print(f"Attempt {attempt+1} failed for {url}: {e}")
            time.sleep(5)
    return None

for idx, row in df.iterrows():
    url = row[xbrl_col]
    company = str(row.get("COMPANY", f"company_{idx}")).replace(" ", "_")
    period = str(row.get("PERIOD", idx)).replace(" ", "_")

    # Download
    xbrl_content = fetch_with_retry(url, retries=3, timeout=120)
    if not xbrl_content:
        print(f"Skipping {url} after retries")
        continue

    try:
        # Parse XML/XBRL
        root = ET.fromstring(xbrl_content)
        data = []
        for elem in root.iter():
            if elem.text and elem.text.strip():
                data.append({
                    "tag": elem.tag,
                    "value": elem.text.strip(),
                    "contextRef": elem.attrib.get("contextRef"),
                    "unitRef": elem.attrib.get("unitRef")
                })

        # Convert to DataFrame
        fact_df = pd.DataFrame(data)

        # Build unique filename
        out_file = f"xbrl_csvs/{company}_{period}.csv"
        fact_df.to_csv(out_file, index=False, encoding="utf-8-sig")

        print(f"✅ Saved: {out_file} ({len(fact_df)} rows)")

    except Exception as e:
        print(f"❌ Parse failed for {url}: {e}")


Attempt 1 failed for https://nsearchives.nseindia.com/corporate/xbrl/INDAS_121161_1515194_20082025041557.xml: HTTPSConnectionPool(host='nsearchives.nseindia.com', port=443): Read timed out. (read timeout=120)


KeyboardInterrupt: 

In [16]:
pip install pandas requests


Note: you may need to restart the kernel to use updated packages.


In [17]:
python embed_xbrl_content_into_csv.py \
  --input "CF-FR-equities-01-01-2005-to-22-08-2025.csv"


SyntaxError: invalid syntax (1388722811.py, line 1)

zsh:1: command not found: python


In [23]:
import os
import pandas as pd

# Root folder containing all company subfolders
root_folder = "/Users/bhookhabhaloo/Downloads/company_xml_csvs"

all_tag_sets = []
all_files = []

# Walk through all subfolders
for company in os.listdir(root_folder):
    company_dir = os.path.join(root_folder, company)
    if not os.path.isdir(company_dir):
        continue
    
    for file in os.listdir(company_dir):
        if file.endswith(".csv"):
            file_path = os.path.join(company_dir, file)
            all_files.append(file_path)

            try:
                df = pd.read_csv(file_path)
                if "tag" in df.columns:
                    tag_set = set(df["tag"].dropna().unique())
                    all_tag_sets.append(tag_set)
            except Exception as e:
                print(f"⚠️ Error reading {file_path}: {e}")

# Find common tags across all files
if all_tag_sets:
    common_tags = set.intersection(*all_tag_sets)
    print(f"✅ Found {len(common_tags)} common tags across {len(all_files)} files")

    # Save common tags to CSV
    common_tags_csv = ( "/Users/bhookhabhaloo/Documents/common_tags.csv")
    pd.DataFrame(sorted(common_tags), columns=["CommonTag"]).to_csv(common_tags_csv, index=False)
    print(f"📂 Saved to {common_tags_csv}")
else:
    print("⚠️ No CSVs found or no tags extracted")


✅ Found 9 common tags across 48213 files
📂 Saved to /Users/bhookhabhaloo/Documents/common_tags.csv


In [24]:
import os
import pandas as pd

# Root folder
root_folder = "/Users/bhookhabhaloo/Downloads/company_xml_csvs"

# Tags to check
required_tags = {"DebtEquityRatio", "ProfitBeforeTax", "OtherIncome", "Revenue", "Expenses"}

# Track results
missing_counts = {tag: 0 for tag in required_tags}
files_checked = 0

# Walk through all subfolders and CSVs
for company in os.listdir(root_folder):
    company_dir = os.path.join(root_folder, company)
    if not os.path.isdir(company_dir):
        continue

    for file in os.listdir(company_dir):
        if file.endswith(".csv"):
            file_path = os.path.join(company_dir, file)
            try:
                df = pd.read_csv(file_path)
                files_checked += 1
                if "tag" not in df.columns:
                    # If Tag column missing, count all as missing
                    for tag in required_tags:
                        missing_counts[tag] += 1
                    continue

                tags_present = set(df["tag"].dropna().unique())
                for tag in required_tags:
                    if tag not in tags_present:
                        missing_counts[tag] += 1

            except Exception as e:
                print(f"⚠️ Error reading {file_path}: {e}")

# Show results
print(f"✅ Total files checked: {files_checked}")
print("🔎 Missing tag counts:")
for tag, count in missing_counts.items():
    print(f"  {tag}: missing in {count} files")

# Save to CSV
output_file = ("/Users/bhookhabhaloo/Documents/missing_tags_summary.csv")
pd.DataFrame(list(missing_counts.items()), columns=["Tag", "MissingInFiles"]).to_csv(output_file, index=False)
print(f"📂 Summary saved to {output_file}")


✅ Total files checked: 48213
🔎 Missing tag counts:
  Expenses: missing in 849 files
  ProfitBeforeTax: missing in 851 files
  OtherIncome: missing in 1 files
  Revenue: missing in 47911 files
  DebtEquityRatio: missing in 35050 files
📂 Summary saved to /Users/bhookhabhaloo/Documents/missing_tags_summary.csv


In [26]:
import os
import pandas as pd
from collections import defaultdict

# Root folder
root_folder = "/Users/bhookhabhaloo/Downloads/company_xml_csvs"

# Dictionary: tag -> set of files it appears in
tag_files = defaultdict(set)

files_checked = 0

for company in os.listdir(root_folder):
    company_dir = os.path.join(root_folder, company)
    if not os.path.isdir(company_dir):
        continue

    for file in os.listdir(company_dir):
        if file.endswith(".csv"):
            file_path = os.path.join(company_dir, file)
            try:
                df = pd.read_csv(file_path)
                files_checked += 1

                if "tag" not in df.columns:
                    continue

                # Unique tags in this file
                tags = set(df["tag"].dropna().unique())
                for tag in tags:
                    tag_files[tag].add(file_path)

            except Exception as e:
                print(f"⚠️ Error reading {file_path}: {e}")

# Build summary: Tag | Count of files present
summary = [(tag, len(files)) for tag, files in tag_files.items()]
summary_df = pd.DataFrame(summary, columns=["Tag", "FileCount"]).sort_values(by="FileCount", ascending=False)

# Save to CSV
output_file = ("/Users/bhookhabhaloo/Documents/all_tags_file_presence.csv")
summary_df.to_csv(output_file, index=False)

print(f"✅ Total files checked: {files_checked}")
print(f"📂 Summary saved to {output_file}")
print(summary_df.head(20))  # show top 20 tags


✅ Total files checked: 48213
📂 Summary saved to /Users/bhookhabhaloo/Documents/all_tags_file_presence.csv
                                                  Tag  FileCount
57                                             Symbol      48213
71                WhetherResultsAreAuditedOrUnaudited      48213
41               NatureOfReportStandaloneConsolidated      48213
43                  DescriptionOfPresentationCurrency      48213
34                                         TaxExpense      48213
18                         DateOfStartOfFinancialYear      48213
33                                   ReportingQuarter      48213
75                                            measure      48213
1                            DateOfEndOfFinancialYear      48213
59                      FaceValueOfEquityShareCapital      48212
3                                         OtherIncome      48212
56                    PaidUpValueOfEquityShareCapital      48212
5                          DateOfEndOfReportingPe

In [ ]:
import os
import pandas as pd
import shutil

# Root folder
root_folder = "/Users/bhookhabhaloo/Downloads/company_xml_csvs"

# Mapping of tags → renamed labels
tag_mapping = {
    "NatureOfReportStandaloneConsolidated": "Standalone/Consolidated",
    "TaxExpense": "Tax Expense",
    "OtherIncome": "Other Income",
    "Income": "Revenue",
    "Expenses": "Expenses",
    "RevenueFromOperations": "Revenue from operation",
    "ProfitBeforeTax": "Profit Before Tax",
    "OtherExpenses": "Other Expenses",
    "ProfitLossForPeriodFromContinuingOperations": "Profit Loss From Continuing Operations",
    "ProfitLossFromDiscontinuedOperationsBeforeTax": "Profit Loss From Discontinued Operations",
    "ProfitLossForPeriod": "Profit Loss",
    "Symbol": "Symbol",
    "DebtEquityRatio": "Debt Equity Ratio",
    "RevenueFromSaleOfServices": "Revenue",
    "RevenueFromSaleOfProduct": "Revenue",
    "Revenue": "Revenue",
    "ProfitLossForThePeriod": "Profit Loss",
    "OtherRevenueFromOperations": "Other Revenue",
    "PercentageOfNpa": "NPA",
    "ProfitLossFromOrdinaryActivitiesBeforeTax": "Other Profit Loss",
    "NonPerformingAssets": "NPA",
    "PercentageOfGrossNpa": "NPA",
    "ProfitLossFromDiscontinuingOperationsBeforeTax": "Profit Loss From Discontinuing Operations",
    "ProfitLossForThePeriodFromContinuingOperations": "Profit Loss From Continuing Operations",
}

# Process each company folder
for company in os.listdir(root_folder):
    company_dir = os.path.join(root_folder, company)
    if not os.path.isdir(company_dir):
        continue

    print(f"📂 Processing company folder: {company}")

    all_symbols = set()

    for file in os.listdir(company_dir):
        if not file.endswith(".csv"):
            continue

        file_path = os.path.join(company_dir, file)
        try:
            df = pd.read_csv(file_path)

            if "Tag" not in df.columns or "Value" not in df.columns:
                print(f"⚠️ Skipped {file_path} (no Tag/Value columns)")
                continue

            # Filter only relevant tags
            df = df[df["Tag"].isin(tag_mapping.keys())].copy()

            # Rename tags
            df["Tag"] = df["Tag"].map(tag_mapping)

            # Track symbol values
            symbol_values = df.loc[df["Tag"] == "Symbol", "Value"].unique()
            if len(symbol_values) > 0:
                all_symbols.update(symbol_values)

            # Save back
            df.to_csv(file_path, index=False)

        except Exception as e:
            print(f"⚠️ Error processing {file_path}: {e}")

    # If all files have the same Symbol, rename folder
    if len(all_symbols) == 1:
        symbol = list(all_symbols)[0]
        safe_symbol = "".join(c if c.isalnum() or c in "._-" else "_" for c in symbol)
        new_dir = os.path.join(root_folder, safe_symbol)

        if company_dir != new_dir:
            print(f"🔄 Renaming folder {company} → {safe_symbol}")
            shutil.move(company_dir, new_dir)


📂 Processing company folder: Quadrant_Future_Tek_Limited
⚠️ Skipped /Users/bhookhabhaloo/Downloads/company_xml_csvs/Quadrant_Future_Tek_Limited/31-Dec-2024_Third_Quarter.csv (no Tag/Value columns)
📂 Processing company folder: Gokul_Refoils_and_Solvent_Limited
⚠️ Skipped /Users/bhookhabhaloo/Downloads/company_xml_csvs/Gokul_Refoils_and_Solvent_Limited/30-Sep-2019_Second_Quarter.csv (no Tag/Value columns)
⚠️ Skipped /Users/bhookhabhaloo/Downloads/company_xml_csvs/Gokul_Refoils_and_Solvent_Limited/30-Jun-2018_First_Quarter.csv (no Tag/Value columns)
⚠️ Skipped /Users/bhookhabhaloo/Downloads/company_xml_csvs/Gokul_Refoils_and_Solvent_Limited/31-Dec-2018_Third_Quarter.csv (no Tag/Value columns)
⚠️ Skipped /Users/bhookhabhaloo/Downloads/company_xml_csvs/Gokul_Refoils_and_Solvent_Limited/31-Mar-2020_Fourth_Quarter.csv (no Tag/Value columns)
⚠️ Skipped /Users/bhookhabhaloo/Downloads/company_xml_csvs/Gokul_Refoils_and_Solvent_Limited/30-Sep-2024_Second_Quarter.csv (no Tag/Value columns)
⚠️ Skip